In [180]:
import numpy as np
import pandas as pd
import geopandas as gpd

#for geocoder
import geopy
from geopy.geocoders import Nominatim

#for reprojecting
import pyproj
from shapely.geometry import Point, Polygon, LineString

import matplotlib.pyplot as plt

from re import search

In [146]:
fp = 'D:/2020-geo/NH_roads.shp'
gdf = gpd.read_file(fp)

In [147]:
gdf.head()

osm_id  code      fclass             name   ref oneway  maxspeed  layer  \
0  4264947  5152    cycleway             None  None      B         0      0   
1  4270144  5124  pedestrian      Dapperplein  None      B         0      0   
2  4270151  5153     footway  Zeeburgerstraat  None      B         0      0   
3  4270806  5152    cycleway     Roomtuintjes  None      B         0      0   
4  4277440  5124  pedestrian       Vondelpark  None      B         0      0   

  bridge tunnel                                           geometry  
0      F      F  LINESTRING (4.92236 52.36544, 4.92237 52.36543...  
1      F      F  LINESTRING (4.92794 52.36198, 4.92802 52.36203...  
2      F      F  LINESTRING (4.92611 52.36633, 4.92607 52.36627...  
3      F      F  LINESTRING (4.93087 52.36594, 4.93082 52.36573...  
4      F      F  LINESTRING (4.88148 52.36157, 4.88168 52.36170...

In [148]:
gdf.crs = {'init': 'epsg:4326'}

In [139]:
bridges = gdf[gdf['bridge']=='T']

In [144]:
bridges.head(50)

osm_id  code        fclass                      name   ref oneway  \
45    4013257  5152      cycleway                      None  None      F   
57    4072737  5155         steps                      None  None      B   
90    4248627  5114     secondary        Smits van Oyenlaan  None      F   
112   4256276  5141       service               Sterrenlaan  None      B   
148   4260740  5152      cycleway               Opetersepad  None      B   
264   4274782  5153       footway                      None  None      B   
275   4275992  5152      cycleway               Sterrenlaan  None      B   
321   4293252  5152      cycleway                  Muntbrug  None      B   
371   4308858  5152      cycleway  Weg der Verenigde Naties  None      B   
376   4310808  5155         steps                      None  None      B   
394   4317938  5155         steps                      None  None      B   
457   4340048  5152      cycleway                      None  None      B   
458   4340765  5152      cycleway                      None  None      B   
464   4342281  5153       footway                      None  None      B   
529   4353321  5152      cycleway             Geldropsedijk  None      B   
570   4360193  5153       footway                      None  None      B   
585   4364802  5152      cycleway              Pelikaanbrug  None      B   
689   4389545  5121  unclassified                Beekstraat  None      B   
693   4389839  5152      cycleway              Socratesbrug  None      B   
802   4413651  5152      cycleway          Hoog Buurloseweg  None      B   
821   4416473  5153       footway                      None  None      B   
822   4416474  5153       footway                      None  None      B   
845   4424482  5152      cycleway                 Trompbrug  None      B   
851   4428102  5152      cycleway                      None  None      B   
855   4428325  5152      cycleway                      None  None      B   
861   4430446  5121  unclassified            Park Oog in Al  None      B   
905   4436686  5153       footway                      None  None      B   
923   4443694  5153       footway                      None  None      B   
925   4443696  5153       footway                      None  None      B   
975   4451529  5153       footway                      None  None      B   
1021  4464167  5153       footway                      None  None      B   
1022  4464169  5153       footway                      None  None      B   
1030  4464178  5153       footway                      None  None      B   
1037  4464316  5153       footway                      None  None      B   
1041  4464326  5152      cycleway                      None  None      B   
1047  4470467  5153       footway                      None  None      B   
1067  4471474  5153       footway                      None  None      B   
1099  4480327  5153       footway                      None  None      B   
1104  4480626  5152      cycleway                      None  None      B   
1166  4495991  5152      cycleway             Leemputtenpad  None      B   
1248  4566054  5152      cycleway                      None  None      B   
1303  4580260  5152      cycleway            Zwartewaterweg  None      B   
1309  4585495  5154          path                      None  None      B   
1332  4587391  5152      cycleway                 Klaverpad  None      B   
1336  4587407  5152      cycleway             Cathalijnepad  None      B   
1417  4624391  5152      cycleway  Cornelis van Beverenbrug  None      B   
1441  4639546  5153       footway                      None  None      B   
3985  4669805  5152      cycleway                      None  None      B   
4471  4670887  5152      cycleway             Moerbeistraat  None      B   
4873  4672127  5115      tertiary              BalloÃ«rveld  None      B   

      maxspeed  layer bridge tunnel  \
45           0      1      T      F   
57           0      1      T      F   
90          8

In [141]:
fig, ax = plt.subplots(figsize=(20,20))
bridges.plot(ax=ax)

In [245]:
#takes the radius in meters, so 10km = 10000
def select_part_data(gdf, city, radius):
    #### 1: take the city name and extract the lat and lon using geocoder #####
    # Define the locator
    locator = Nominatim(user_agent="myGeocoder")
    city = select_city
    city_loc = locator.geocode(city)

    # Then, you can print the coordinates:
    #print("Latitude = {}, Longitude = {}".format(city_loc.latitude, city_loc.longitude))
    
    #Den Helder: 52.956090, 4.740161
    #Amsterdam: 52.377803, 4.899968
    # Create GeoDataFrame
    citydf = gpd.GeoDataFrame([[Point(4.899968, 52.377803)]], geometry='geometry', crs={'init': 'epsg:4326'}, columns=['geometry'])
    
    #### 2. Take the city and reproject using that point as the center.
    # Define the projection using the coordinates of our city point (city_loc.latitude and city_loc.longitude) as the center point
    # The .srs here returns the Proj4-string presentation of the projection
    aeqd = pyproj.Proj(proj='aeqd', ellps='WGS84', datum='WGS84', lat_0=city_loc.latitude, lon_0=city_loc.longitude).srs
    
    citydf = citydf.to_crs(crs=aeqd)
     
    #### 3. Reproject the other street data using the same center. 
    # Create a copy
    gdf_aeqd = gdf.copy()
    
    # Reproject to aeqd projection that we defined earlier and calculate buffer around street
    gdf_aeqd = gdf_aeqd.to_crs(crs=aeqd)
    gdf_buffer = gdf_aeqd.copy()
    gdf_buffer.geometry = gdf_aeqd.geometry.buffer(10)
    
    
    #### 4. Create a buffer using the radius around the city
    city_loc_radius = citydf.buffer(radius)
    city_loc_df = gpd.GeoDataFrame(geometry=city_loc_radius)
    
    print(gdf_buffer)
    print(city_loc_df)
    
    ### 5. Look at intersection
    intersection = gpd.overlay(city_loc_df, gdf_buffer, how='intersection')
    print(intersection)
    print(len(intersection))
    fig, ax = plt.subplots(figsize=(20,20))
    intersection.plot(ax=ax)
    print(intersection)
    
    return intersection

In [246]:
den_helder = select_part_data(gdf, 'Den Helder', 10000)

           osm_id  code      fclass             name   ref oneway  maxspeed  \
0         4264947  5152    cycleway             None  None      B         0   
1         4270144  5124  pedestrian      Dapperplein  None      B         0   
2         4270151  5153     footway  Zeeburgerstraat  None      B         0   
3         4270806  5152    cycleway     Roomtuintjes  None      B         0   
4         4277440  5124  pedestrian       Vondelpark  None      B         0   
...           ...   ...         ...              ...   ...    ...       ...   
267605  818850585  5153     footway             None  None      B         0   
267606  818850586  5153     footway        Oliemolen  None      B         0   
267607  818851427  5153     footway             None  None      B         0   
267608  818851428  5153     footway             None  None      B         0   
267609  818851429  5153     footway             None  None      B         0   

        layer bridge tunnel                        

In [247]:
den_helder[den_helder['name']!= 'None']

osm_id  code        fclass                    name   ref oneway  \
0      786342247  5154          path                    None  None      B   
1      129376721  5152      cycleway                    None  None      B   
2      786481854  5154          path                    None  None      B   
3      791552540  5141       service                    None  None      B   
4      786481853  5154          path                    None  None      B   
...          ...   ...           ...                     ...   ...    ...   
70849    7389672  5121  unclassified           Casablancaweg  None      B   
70850    7389398  5122   residential  Wethouder Rijkeboerweg  None      B   
70851    7389417  5121  unclassified                    None  None      F   
70852    7389608  5122   residential        Zijkanaal F Oost  None      B   
70853    7389676  5153       footway                    None  None      B   

       maxspeed  layer bridge tunnel  \
0             0      0      F      F   
1             0      0      F      F   
2             0      0      F      F   
3             0      0      F      F   
4             0      0      F      F   
...         ...    ...    ...    ...   
70849         0      0      F      F   
70850        30      0      F      F   
70851        30      0      F      F   
70852         0      0      F      F   
70853         0      0      F      F   

                                                geometry  
0      POLYGON ((8924.424 -68983.717, 8912.889 -68963...  
1      POLYGON ((9100.414 -68973.612, 9077.391 -68992...  
2      POLYGON ((8938.051 -68987.569, 8937.173 -68988...  
3      POLYGON ((9354.426 -68974.418, 9354.930 -68973...  
4      POLYGON ((8974.701 -68944.000, 8975.581 -68943...  
...                                                  ...  
70849  POLYGON ((-4615.890 -61228.959, -4610.534 -612...  
70850  POLYGON ((-4946.709 -62891.499, -4945.726 -628...  
70851  POLYGON ((-4947.030 -62893.662, -4944.071 -628...  
70852  POLYGON ((-4922.068 -62725.382, -4919.131 -627...  
70853  POLYGON ((-4894.683 -62540.764, -4891.714 -625...  

[70854 rows x 11 columns]

In [254]:
conditions = [
    (den_helder['name'].str.contains(pat='weg') ==True),
    (den_helder['name'].str.contains(pat='straat')==True),
    (den_helder['name'].str.contains(pat='dijk')==True),
    (den_helder['name'].str.contains(pat='laan')==True),
    (den_helder['name'].str.contains(pat='gracht')==True),
    (den_helder['name'].str.contains(pat='kade')==True),]
choices = ['weg', 'straat', 'dijk','laan','plein','hof']
color = ['#1871F5', '#03A35D', '#FFB101', '#D9402C', '#F46D8D', '#9941BF']
den_helder['soort'] = np.select(conditions, choices, default='overig')
den_helder['color'] = np.select(conditions, color, default='#F1F8F5')
print(den_helder)

          osm_id  code        fclass                    name   ref oneway  \
0      786342247  5154          path                    None  None      B   
1      129376721  5152      cycleway                    None  None      B   
2      786481854  5154          path                    None  None      B   
3      791552540  5141       service                    None  None      B   
4      786481853  5154          path                    None  None      B   
...          ...   ...           ...                     ...   ...    ...   
70849    7389672  5121  unclassified           Casablancaweg  None      B   
70850    7389398  5122   residential  Wethouder Rijkeboerweg  None      B   
70851    7389417  5121  unclassified                    None  None      F   
70852    7389608  5122   residential        Zijkanaal F Oost  None      B   
70853    7389676  5153       footway                    None  None      B   

       maxspeed  layer bridge tunnel  \
0             0      0      F      

In [227]:
den_helder['soort'].value_counts()

overig    1587
straat    1224
weg        448
laan       166
plein       67
hof         42
dijk         9
Name: soort, dtype: int64

In [255]:
fig, ax = plt.subplots(figsize=(25,25))
den_helder.plot(ax=ax, color=den_helder['color'])
plt.savefig('streets.png')
